# Clustering - K-means 

**Sommaire**
1. Introduction
2. Programmation de l'algorithme
3. Création des données
4. Graphiques et fonctionnement

# Introduction
L'algorithme K-means est un algorithme de clustering **non-supervisé**.</br>
On choisit K points aléatoirement et on les choisit comme barycentres. Puis pour chaque point, on l'assigne au cluster du barycentre le plus proche. Puis on recalcule les barycentres de temps en temps jusqu'à convergence.


In [0]:
# Importation des librairies
import numpy as np
import matplotlib.pyplot as plt
from random import randint,shuffle

Avant de nous lancer dans l'écriture de l'algorithme, il faut prendre en compte un autre paramètre de K-Means : **La distance choisie**.</br>
Le choix de la distance aura des conséquences sur les résultats. Dans un premier temps nous utiliserons la distance euclidienne, mais il sera intéressant par la suite de comparer les résultats pour différentes distances.</br>
**Distance euclidienne**
C'est celle qu'on utilise de manière usuelle, et que nous utilisions précédement, je remet donc le résultat:</br>
d(a,b) = √((xa-xb)²+(ya-yb))

**Distance de Manhattan**
Elle découle de la valeur absolue: </br>
d(a, b) = |xb – xa| + |yb – ya|</br>

**Distance aux échecs**
Elle découle elle aussi de la valeur absolue, mais prend en compte le maximum.</br>
d(a, b) = max(|xb – xa|, |yb – ya|)</br>



In [0]:
# Les distances

def distance_quadratique(pt1,pt2): # Distance quadratique/euclidienne
  return sum((pt1-pt2)**2)**(1/2)

def distance_manhattan(pt1,pt2):   # Distance de Manhattan (utilisant la valeur absolue)
  return sum(abs(pt1-pt2))

def distance_echecs(pt1,pt2):      # Distance des échecs (le maximum, c'est la norme infinie)
  return max(abs(pt1-pt2))


# Programmation de l'algorithme
Nous allons pouvoir programmer l'algorithme.</br>
Nous allons stocker les clusters comme une liste de K listes, correspondant aux K clusters.</br>
Chaque liste (de cluster) contiendra les indices des points (plutôt que le point en lui même).

In [0]:
def kMeans(K,points,N=5,distance=distance_quadratique):
  
  clusters = [[] for i in range(K)]
  barycentres = [0 for i in range(K)]
  visites = []
  
  for i in range(K):
    indice = randint(0,len(points)-1)
    if indice not in visites:
      clusters[i].append(indice)
      visites.append(indice)
  
  N=0
  while N<13:
    for j in range(K):
          bary = sum([points[indice] for indice in clusters[j]])/len(clusters[j])
          barycentres[j] = bary

    for i_point in range(len(points)):

      dmin = distance(points[i_point],barycentres[0])
      imin = 0
      for i_cluster in range(1,K):
        d = distance(points[i_point],barycentres[i_cluster])
        if d<dmin:
          dmin = d
          imin = i_cluster
      clusters[imin].append(i_point)
    N+=1
    
  return clusters,barycentres
        
    
  

In [0]:
# Pour tester s'il n'y a pas d'erreur dans l'algorithme, nous vérifierons par la suite si cela semble fonctionner
a,b = kMeans(2,[np.array([2,1]),np.array([0,0]),np.array([5,5])])

Maintenant que l'algorithme a été écrit, il va falloir le tester. Et pour le tester, il va nous falloir des données.

# Création des données
Maintenant que nous avons codé l'algorithme, il nous faut un moyen de le tester. Pour cela nous utiliserons une base de données assez simple que nous allons créer. Cette base de données sera utilisée dans d'autres fichier Jupyters.</br>
Les données d'origine peuvent être de tout type (Des tailles, des couleurs, des dates, ...), et il est généralement nécessaire d'effectuer des transformations pour les mettre sous la meilleure forme pour utiliser un algorithme de classification.</br>
Cette partie ne sera pas traitée, on supposera donc que nos données ont été traitées et qu'elles sont sous forme de vecteur dans un espace de dimension variable (ici pour simplifier on se placera en dimension 2, facilement visualisable).</br></br>

Dans notre cas, nous allons générer des données avec une répartition normale autour de certaines zones.

In [0]:

# Les paramètres importants
nbr_clusters=4
nbr_initialisation=100
nbr_evalutation=200

# Les listes
init_points=[]
init_labels=[]
eval_points=[]
eval_labels=[]


donnees_initialisation=[[] for i in range(nbr_clusters)]  #Tableau avec les données que l'on donnera pour l'initialisation de l'algorithme

centres_generation=[np.array([0.8,0.8]),np.array([0.8,-0.8]),np.array([-0.8,-0.8]),np.array([-0.8,0.8])] 

# Création des données d'initialisation
for i in range(nbr_initialisation):
  indice=np.random.randint(0,nbr_clusters)
  point=centres_generation[indice]+np.random.normal(scale=0.2,size=2) # Répartition normale autour d'un barycentre
  init_points.append(point)
  init_labels.append(indice)
  donnees_initialisation[indice].append(point)

# Création des données de test
for i in range(nbr_evalutation):
  indice=np.random.randint(0,nbr_clusters)
  point=centres_generation[indice]+np.random.normal(scale=0.2,size=2) # Répartition normale autour d'un barycentre
  eval_points.append(point)
  eval_labels.append(indice)
  
print('Les données ont été générées !')
print('Nombre de clusters: {}'.format(nbr_clusters))
print('Nombre de points pour l\'initialisation: {}'.format(nbr_initialisation))
print('Nombre de points pour l\'évaluation: {}'.format(nbr_evalutation))

Maintenant que nous avons créé les données, je vous propose de les visualiser pour mieux comprendre ce que nous avons généré.

In [0]:
# On définit les limites du graphique
lim=1.5
plt.xlim([-lim,lim])
plt.ylim([-lim,lim])

for i in range(nbr_initialisation):
  point=init_points[i]
  label=init_labels[i]
  plt.plot(point[0],point[1],color="b",marker="+") # On affiche chaque point avec la couleur de son cluster
  
plt.show()

# Efficacité de l'algorithme
Maintenant que nous avons créé notre algorithme, nous allons pouvoir le tester sur un plus grand nombre d'échantillons, pour vérifier si l'algorithme fonctionne correctement (ie que les résultats semblent corrects)</br>
Le raisonnement statistique (sur un grand nombre d'éléments) nous permet de voir si de manière générale, l'algorithme sort des résultats cohérents.

In [0]:
K = 4

clusters,barycentres = kMeans(K,init_points,distance=distance_quadratique)


plt.figure()
couleurs=['r','g','b','y']
for n,cluster in enumerate(clusters):
  for pt in cluster:
    plt.plot(init_points[pt][0],init_points[pt][1],color=couleurs[n],marker="o")
plt.show()


# Pour aller plus loin

Nous avons donc vu l'algorithme K-Means dans sa forme la plus simple, mais il est tout à fait possible d'aller plus loin dans son élaboration.




## Test des distances

Cherchons à savoir exactement ce que nous donne notre algorithme. Je vous propose donc d'afficher les sorties de l'algorithme.
Les entrées sont les coordonnées d'un point, ici donc les coordonnées sont liées aux pixels.</br>
La sortie est le cluster choisi, que l'on représente par la couleur du pixel (en fonction du cluster).</br>
Voici ce que cela donne dans ce cas ici présent.</br></br>
Note: Ce type de représentation est très pratique pour identifier l'efficacité d'un algorithme 'au nez'.


In [0]:
# Un affichage plus recherché
plt.figure(figsize=(20,10))
lim=1.5
plt.xlim([-lim,lim])
plt.ylim([-lim,lim])

#Couleurs
couleurs=['r','g','b','y']
couleurs_graph=[[1,0,0],[0,1,0],[0,0,1],[0,1,1]]

K = 4

clusters,barycentres = kMeans(K,init_points,distance=distance_quadratique)

plt.title("Affichage des données d'initialisation")
plt.subplot(221)
plt.axis('equal')
for n,cluster in enumerate(clusters):
  for pt in cluster:
    plt.plot(init_points[pt][0],init_points[pt][1],color=couleurs[n],marker="o")


# On affiche les représentations des sorties de ces algos selon les distances utilisées


types_distances=[distance_quadratique,distance_manhattan,distance_echecs]
nom_distances=['distance Quadratique/Euclidienne','distance de Manhattan','distance des échecs']
for k in range(len(types_distances)):
  if k==0: plt.subplot(222)
  if k==1: plt.subplot(223)
  if k==2: plt.subplot(224)
    
  dist=types_distances[k]

  width=50
 
  image=np.zeros((width,width,3))
  points = []
  for i in range(width):
    for j in range(width):
      x=(i/width-0.5)*2*lim
      y=(j/width-0.5)*2*lim
      point=np.array([x,y])
      
      dmin = dist(point,barycentres[0])
      imin = 0
      for i_cluster in range(1,K):
        d = dist(point,barycentres[i_cluster])
        if d<dmin:
          dmin = d
          imin = i_cluster
      
      image[width-1-j,i]=couleurs_graph[imin]
  plt.title('Avec la '+nom_distances[k])
  plt.imshow(image) 


On peut remarquer que les résultats sont différents en fonction de la distance employée.</br>
Néanmoins, les données qui sont en entrée sont suffisament claires pour que pour ces distances, le résultat reste globalement le même.</br>


## Choix de la valeur de K

La valeur de K est également difficile à trouver, surtout quand on a peu d'informations sur les données en entrée.</br>
Dans ce cas là, plusieurs méthodes existent:</br>

La méthode du "Gap Statistic":</br>
https://statweb.stanford.edu/~gwalther/gap

La méthode de l'Indice de Davies-Boulding:</br> https://en.wikipedia.org/wiki/Davies%E2%80%93Bouldin_index</br>
https://openclassrooms.com/en/courses/4379436-explorez-vos-donnees-avec-des-algorithmes-non-supervises/4379556-definissez-les-criteres-que-doit-satisfaire-votre-clustering</br>

La méthode de la silhouette:</br>
https://openclassrooms.com/en/courses/4379436-explorez-vos-donnees-avec-des-algorithmes-non-supervises/4379556-definissez-les-criteres-que-doit-satisfaire-votre-clustering</br>